# Assignment: Classification

Classification refers to categorizing the given data into classes. For example,
- Given an image of hand-written character, identifying the character (multi-class classification)
- Given an image, annotating it with all the objects present in the image (multi-label classification)
- Classifying an email as spam or non-spam (binary classification)
- Classifying a tumor as benign or malignant and so on

In this assignment, we will be building a classifier to classify emails as spam or non-spam. We will be using the Kaggle dataset [Spam or Not Spam Dataset](https://www.kaggle.com/datasets/ozlerhakan/spam-or-not-spam-dataset?resource=download) for this task. 

**Note**: You cannot load any libraries other than the mentioned ones.




### Data pre-processing
The first step in every machine learning algorithm is to process the raw data in some meaningful representations. We will be using the [Bag-of-Words](https://towardsdatascience.com/a-simple-explanation-of-the-bag-of-words-model-b88fc4f4971) representation to process the text. It comprises of following steps:

- Process emails line-by-line to extract all the words.
- Replace extracted words by their stem (root) word. This is known as stemming and lematization.
- Remove stop words like and, or, is, am, and so on.
- Assign a unique index to each word. This forms the vocabulary.
- Represent each email as a binary vector of length equal to the size of the vocabulary such that the $i^{th}$ element of the vector is 1 iff the $i^th$ word is present in the email.

Here we provide you with the function signature along with the expected functionality. You are expected to complete them accordingly. 

In [12]:
vocab={-1:"#"}

In [13]:
import numpy as np
from nltk.stem import PorterStemmer
from nltk.corpus import stopwords

# takes an email as an argument
# read email line-by-line and extract all the words
# return list of extracted words
def read_email(email):
  words=email.split()
  return words
  
# takes a list of words as an argument
# replace each word by their stem word
# return list of stem words
def stemming(words):
  stemmer=PorterStemmer()
  stem_words = [stemmer.stem(word) for word in words]
  return stem_words

# takes a list of stem-words as an argument
# remove stop words
# return list of stem words after removing stop words
def remove_stop_words(stem_words):
  stop_words = set(stopwords.words('english'))
  stem_no_stop_words=[w for w in stem_words if not w.lower() in stop_words]
  """
  stem_no_stop_words=[]
  for word in stem_words:
    if word.lower() not in stopwords:
        stem_no_stop_words.append(word.lower())
  """
  return stem_no_stop_words

# takes a list of stem-words as an argument
# add new words to the vocabulary and assign a unique index to them
# returns new vocabulary
def build_vocabulary(stem_no_stop_words):
  for word in stem_no_stop_words:
    if word not in vocab.values():
        key=max(vocab.keys())+1
        vocab[key]=word
  return vocab

# takes a list of stem-words and vocabulary as an argument
# returns bow representation
def get_bow(stem_no_stop_words,vocab):
  email_bow=np.zeros(len(vocab), dtype = int)
  for key in vocab.keys():
    if vocab[key] in stem_no_stop_words:
        email_bow[key]=1
  return email_bow

# read the entire dataset
# convert emails to bow and maintain their labels
# call function text_to_bow()
def read_data():
  f=open("spam_or_not_spam.csv",encoding='utf-8')
  f.readline()
  i=0
  for row in f:
    email=row[:-4]
    value=int(row[-2:])
    words=remove_stop_words(stemming(read_email(email)))
    build_vocabulary(words)
    i=i+1
  f.close()
  f=open("spam_or_not_spam.csv",encoding='utf-8')
  f.readline()
  vocab.pop(-1)
  data=np.zeros([i,len(vocab)+1],dtype=int)
  j=0
  for row in f:
    email=row[:-4]
    value=int(row[-2:-1])
    words=remove_stop_words(stemming(read_email(email)))
    mail_data=get_bow(words,vocab)
    data[j][:-1]=mail_data
    data[j][-1]=value
    j=j+1
  f.close()
  return data

In [14]:
data=read_data()
print(data[0][:])

[1 1 1 ... 0 0 0]


In [15]:
print(data[:,:-1])

[[1 1 1 ... 0 0 0]
 [0 0 1 ... 0 0 0]
 [0 0 1 ... 0 0 0]
 ...
 [0 0 1 ... 0 0 0]
 [0 0 1 ... 0 0 0]
 [0 0 1 ... 1 1 1]]


In [16]:
print(data.shape)

(3000, 25750)


### Data Visualization
Let's understand the data distribution
- Visualize the frequency of word-occurence in all the emails(spam + non-spam)
- Visualize the freuency of word-occurence for spam and non-spam emails separately

In [5]:
import matplotlib.pyplot as plt

# visuallze data distribution
def data_vis(data):
  freq={}
  freq1={}
  freq0={}
  for word in vocab.values():
        freq[word]=0
        freq1[word]=0
        freq0[word]=0
  for i in range(data.shape[1]-1):
    for j in range(data.shape[0]):
        freq[vocab[i]]=freq[vocab[i]]+data[j][i]
        if data[j][-1]==1:
            freq1[vocab[i]]=freq1[vocab[i]]+data[j][i]
        if data[j][-1]==0:
            freq0[vocab[i]]=freq0[vocab[i]]+data[j][i]
  for word in vocab.values():
    if freq[word]<500:
        freq.pop(word)
    if freq1[word]<400:
        freq1.pop(word)
    if freq0[word]<200:
        freq0.pop(word)
  words=list(freq.keys())
  freq_list=list(freq.values())
  plt.figure(figsize=(400,200))
  plt.bar(words,freq_list)
  plt.title("All Emails")  
  plt.show()
    
  words=list(freq1.keys())
  freq_list1=list(freq1.values())
  plt.bar(words,freq_list1)
  plt.title("Spam Mails")  
  plt.show()
    
  words=list(freq0.keys())
  freq_list0=list(freq0.values())
  plt.figure(figsize=(400,100))
  plt.bar(words,freq_list0)
  plt.title("Non-spam Mails")  
  plt.show()
    
  return 0

data_vis(data)

KeyboardInterrupt: 

In [17]:
freq={}
freq1={}
freq0={}
for word in vocab.values():
    freq[word]=0
    freq1[word]=0
    freq0[word]=0
for i in range(data.shape[1]-1):
    for j in range(data.shape[0]):
        freq[vocab[i]]=freq[vocab[i]]+data[j][i]
        if data[j][-1]==1:
            freq1[vocab[i]]=freq1[vocab[i]]+data[j][i]
        if data[j][-1]==0:
            freq0[vocab[i]]=freq0[vocab[i]]+data[j][i]
for word in vocab.values():
    if freq[word]<500:
        freq.pop(word)
    if freq1[word]<400:
        freq1.pop(word)
    if freq0[word]<200:
        freq0.pop(word)
words=list(freq.keys())
freq_list=list(freq.values())

words1=list(freq1.keys())
freq_list1=list(freq1.values())

words0=list(freq0.keys())
freq_list0=list(freq0.values())

figure, axis = plt.subplots(3, figsize=(400,200))

axis[0].bar(words,freq_list)
axis[0].set_title("All Mails")
.xticks(labels=words, rotation ='vertical')

  
axis[1].bar(words1,freq_list1)
axis[1].set_title("Spam Mails")

axis[2].bar(words0,freq_list0)
axis[2].set_title("Non-Spam Mails")
  
plt.show()

SyntaxError: invalid syntax (Temp/ipykernel_5152/1575238458.py, line 35)

In [20]:
import matplotlib.pyplot as plt

# visuallze data distribution
def data_vis(data):
  freq={}
  freq1={}
  freq0={}
  for word in vocab.values():
        freq[word]=0
        freq1[word]=0
        freq0[word]=0
  for i in range(data.shape[1]-1):
    for j in range(data.shape[0]):
        freq[vocab[i]]=freq[vocab[i]]+data[j][i]
        if data[j][-1]==1:
            freq1[vocab[i]]=freq1[vocab[i]]+data[j][i]
        if data[j][-1]==0:
            freq0[vocab[i]]=freq0[vocab[i]]+data[j][i]
  for word in vocab.values():
    if freq[word]<100:
        freq.pop(word)
        freq1.pop(word)
        freq0.pop(word)  
  words=list(freq.keys())
  xax=range(len(words))

  freq_list=list(freq.values())
  plt.figure(figsize=(400,200))
  plt.bar(words,freq_list)
  plt.title("All Emails")
  plt.xticks(xax,words, rotation ='vertical')
  plt.show()
 
  freq_list1=list(freq1.values())
  plt.figure(figsize=(400,200))
  plt.bar(words,freq_list1)
  plt.title("Spam Mails")
  plt.xticks(xax,words, rotation ='vertical')
  plt.show()
    
  freq_list0=list(freq0.values())
  plt.figure(figsize=(400,200))
  plt.bar(words,freq_list0)
  plt.title("Non-spam Mails")
  plt.xticks(xax,words, rotation ='vertical')
  plt.show()
    
  return 0

data_vis(data)

0

In [25]:
print(freq)

{'date': 830, 'number': 2476, 'messag': 684, 'thi': 1782, 'like': 801, 'time': 837, 'list': 1151, 'use': 1181, 'url': 2509, 'work': 656, 'one': 869, 'get': 1008, 'think': 506, '_______________________________________________': 634, 'mail': 1065, 'wa': 854, 'free': 547, 'email': 744, 'want': 530, 'make': 623, 'new': 682, 'go': 565, 'ha': 834, 'becaus': 515, 'onli': 716, 'wrote': 769, 'peopl': 503, 'ani': 719, 'also': 526, 'need': 509, 'would': 679, 'user': 555, 'know': 504}


### Learn a Classifier
Split the dataset randomly in the ratio 80:20 as the training and test dataset. Use only training dataset to learn the classifier. No test data should be used during training. Test data will only be used during evaluation.

Now let us try to use ML algorithms to classify emails as spam or non-spam. You are supposed to implement [SVM](https://scikit-learn.org/stable/modules/svm.html) and [K-Nearest Neighbour](https://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html) algorithm available in scikit-learn using the same training dataset for both.

In [26]:
from sklearn.neighbors import KNeighborsClassifier
from sklearn import svm

# split dataset
def split(data):
  np.random.shuffle(data)
  lim=int(0.8*data.shape[0])
  train_data, test_data = data[:lim,:], data[lim:,:]
  return train_data, test_data

# learn a SVM model
# use the model to make prediction
# return the model predictions on train and test dataset
def svm_classifier(train_data, test_data):
  classifier=svm.SVC()
  x=train_data[:,:-1]
  y=train_data[:,-1]
  classifier.fit(x,y)
  predict_labels=classifier.predict(test_data[:,:-1])  
  return predict_labels

# implement k-NN algorithm
# use the model to make prediction
# return the model predictions on train and test dataset
def knn_classifier(train_data, test_data):
  classifier=KNeighborsClassifier()
  x=train_data[:,:-1]
  y=train_data[:,-1]
  classifier.fit(x,y)
  predict_labels=classifier.predict(test_data[:,:-1])  
  return predict_labels

train_data, test_data = split(data)
svm_test_predictions = svm_classifier(train_data, test_data)
knn_test_predictions = knn_classifier(train_data, test_data)

### Model Evaluation
Compare the SVM and k-NN model using metrics
- Accuracy
- [AUC score](https://scikit-learn.org/stable/modules/generated/sklearn.metrics.auc.html)


In [27]:
from sklearn import metrics

# compute accuracy 
def compute_accuracy(true_labels, predicted_labels):
  acc=metrics.accuracy_score(true_labels, predicted_labels)
  return acc

# compute AUC score 
def compute_auc(true_labels, predicted_labels):
  fpr,tpr, thresholds = metrics.roc_curve(true_labels, predicted_labels)
  auc=metrics.auc(fpr, tpr)
  return auc

# write code to print train and test accuracy and AUC score of SVM and k-NN classifier
print("Accuracry of SVM",compute_accuracy(test_data[:,-1],svm_test_predictions))
print("Accuracry of KNN",compute_accuracy(test_data[:,-1],knn_test_predictions),"\n")
print("AUC of SVM",compute_auc(test_data[:,-1],svm_test_predictions))
print("AUC of KNN",compute_auc(test_data[:,-1],knn_test_predictions))

Accuracry of SVM 0.9816666666666667
Accuracry of KNN 0.7766666666666666 

AUC of SVM 0.9444444444444444
AUC of KNN 0.8460049597774149
